In [1]:
import requests
import matplotlib.pyplot as plt
import random
from bs4 import BeautifulSoup
import time
import urllib.parse as urlparse
from graphql_query import Operation, Query

In [2]:
#!pip install graphql_query

In [3]:
# Access the Yelp website data using the Yelp API

In [4]:
YELP_TOKEN = "7jaJrr_nORNoRd8qBCPDSqvbRtSkFcDYjxwKF3p5pRHtpPjO47_OlI2ClDTfeOnFqGBSphKddjEEMULXjtP6iljynEelfGiKE7I3BUww8opeMTr6JQoKPKHxFzWPZXYx"

In [5]:
r = requests.get("https://api.yelp.com/v3/businesses/search?location=Toronto&limit=50", headers={"Authorization": "Bearer %s" % YELP_TOKEN})

In [6]:
print(r.status_code, r.reason, r.content)

200 OK b'{"businesses": [{"id": "r_BrIgzYcwo1NAuG9dLbpg", "alias": "pai-northern-thai-kitchen-toronto-5", "name": "Pai Northern Thai Kitchen", "image_url": "https://s3-media4.fl.yelpcdn.com/bphoto/uAnTcmLEQJWkCUOtvZMALA/o.jpg", "is_closed": false, "url": "https://www.yelp.com/biz/pai-northern-thai-kitchen-toronto-5?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ", "review_count": 3562, "categories": [{"alias": "thai", "title": "Thai"}], "rating": 4.5, "coordinates": {"latitude": 43.64784, "longitude": -79.38872}, "transactions": [], "price": "$$", "location": {"address1": "18 Duncan Street", "address2": "", "address3": "", "city": "Toronto", "zip_code": "M5H 3G8", "country": "CA", "state": "ON", "display_address": ["18 Duncan Street", "Toronto, ON M5H 3G8", "Canada"]}, "phone": "+14169014724", "display_phone": "+1 416-901-4724", "distance": 3009.3347434869856}, {"id": "Yl2TN9c23ZGLUBSD9ks5Uw", "alias": 

In [7]:
r.json()['businesses']

[{'id': 'r_BrIgzYcwo1NAuG9dLbpg',
  'alias': 'pai-northern-thai-kitchen-toronto-5',
  'name': 'Pai Northern Thai Kitchen',
  'image_url': 'https://s3-media4.fl.yelpcdn.com/bphoto/uAnTcmLEQJWkCUOtvZMALA/o.jpg',
  'is_closed': False,
  'url': 'https://www.yelp.com/biz/pai-northern-thai-kitchen-toronto-5?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ',
  'review_count': 3562,
  'categories': [{'alias': 'thai', 'title': 'Thai'}],
  'rating': 4.5,
  'coordinates': {'latitude': 43.64784, 'longitude': -79.38872},
  'transactions': [],
  'price': '$$',
  'location': {'address1': '18 Duncan Street',
   'address2': '',
   'address3': '',
   'city': 'Toronto',
   'zip_code': 'M5H 3G8',
   'country': 'CA',
   'state': 'ON',
   'display_address': ['18 Duncan Street', 'Toronto, ON M5H 3G8', 'Canada']},
  'phone': '+14169014724',
  'display_phone': '+1 416-901-4724',
  'distance': 3009.3347434869856},
 {'id': 'Yl2TN9

In [8]:
# Get a list of URLs for each business
URLS = [x['url'] for x in r.json()['businesses']]
URLS[:10]

['https://www.yelp.com/biz/pai-northern-thai-kitchen-toronto-5?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ',
 'https://www.yelp.com/biz/byblos-toronto-2?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ',
 'https://www.yelp.com/biz/osteria-giulia-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ',
 'https://www.yelp.com/biz/richmond-station-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ',
 'https://www.yelp.com/biz/scaramouche-restaurant-pasta-bar-and-grill-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ',
 'https://www.yelp.com/biz/kinka-izakaya-or

In [9]:
len(URLS)

50

In [10]:
# Create a list to store the data
collected_data = []

# Collect Review Data

### Class balance issue

- collect 10, 1,2 and 3 star reviews
- collect 15 4 and 5 star reviews
- if we set the threshold for positive reviews as reviews that have more than 3 stars, then we should have 30 positive and 30 negative reviews for each business
- in addition, we will filter reviews for only those written by elite Yelp users

In [14]:
# Create a function to extract reviews from a url
def extract_reviews(bizURL, collected_data):
    
    # Get the URLS for each star rating page
    bizURLS = [bizURL + '&sort_by=elites_desc&rr=%s'% str(i) for i in range(1, 6)]
    bizURLS.insert(4, bizURL + '&start=10&sort_by=elites_desc&rr=4')
    bizURLS.append(bizURL + '&start=10&sort_by=elites_desc&rr=5')
    
    for url in bizURLS:
        
        # Store star rating
        rating = int(url[-1])
        
        # Store positive/negative based on rating
        sentiment = 'negative'
        if rating > 3:
            sentiment = 'positive'
        
        # Visit page
        r = requests.get(url, headers={"Authorization": "Bearer %s" % YELP_TOKEN})
        # print response
        if r.status_code != 200:
            print(r.status_code, r.reason)
        
        # Get text from page
        html = r.text
        
        # Create BeautifulSoup object
        soup = BeautifulSoup(html, 'html.parser')
        
        # Get the reviews from the page
        try:
            reviews = [p.get_text() for p in soup.find(id="reviews").find_all('p', class_=["comment__09f24__D0cxf css-qgunke"])]
        except AttributeError:
            continue
        
        # Check if url is the second page of 4/5 star reviews
        # and alter the number of reviews if so
        if '&start=10' in url:
            reviews = reviews[:5]
        
        # Append the reviews to the collected_data list
        for review in reviews:
            collected_data.append([review, sentiment])

In [15]:
# Collect review data from the URLS given
for url in URLS:
    print(url)
    extract_reviews(url, collected_data)

https://www.yelp.com/biz/pai-northern-thai-kitchen-toronto-5?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/byblos-toronto-2?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/osteria-giulia-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/richmond-station-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/scaramouche-restaurant-pasta-bar-and-grill-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/kinka-izakaya-original-toronto-4?adjus

https://www.yelp.com/biz/kintaro-izakaya-toronto-3?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/the-carbon-bar-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/holy-cow-japanese-steakhouse-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/the-house-on-parliament-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ
https://www.yelp.com/biz/the-oxley-toronto?adjust_creative=D6QHIFsVWWEKcr6R9_3SXQ&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=D6QHIFsVWWEKcr6R9_3SXQ


In [18]:
collected_data

[["Long wait as expected since I was looking forward to trying this place. The hostess was friendly and quick to seat me. As a disclaimer, I completely empathize with employees within the service industry; particularly in these touristy areas which become extremely busy, so I always have patience and understanding if things take a while. It can be super overwhelming and anxiety can take over, so I understand mishaps. However, when employees are blatantly rude and inattentive, it should be brought to a supervisor's attention so they can be corrected.I was seated and was promptly greeted by a waitress. I ordered water, waited 30 minutes for my waitress to return to take my order as she said she'll be right back to grab me a menu -- I never saw her again. Went up to the bar politely asking if I could place an order, whenever they had a moment (not even requesting to sit there since I understand the seating arrangements for reservations). They rudely said I needed to be checked in in order

In [20]:
review_features = [(x[0].split(' '), x[1]) for x in collected_data]
review_features

[(['Long',
   'wait',
   'as',
   'expected',
   'since',
   'I',
   'was',
   'looking',
   'forward',
   'to',
   'trying',
   'this',
   'place.',
   'The',
   'hostess',
   'was',
   'friendly',
   'and',
   'quick',
   'to',
   'seat',
   'me.',
   'As',
   'a',
   'disclaimer,',
   'I',
   'completely',
   'empathize',
   'with',
   'employees',
   'within',
   'the',
   'service',
   'industry;',
   'particularly',
   'in',
   'these',
   'touristy',
   'areas',
   'which',
   'become',
   'extremely',
   'busy,',
   'so',
   'I',
   'always',
   'have',
   'patience',
   'and',
   'understanding',
   'if',
   'things',
   'take',
   'a',
   'while.',
   'It',
   'can',
   'be',
   'super',
   'overwhelming',
   'and',
   'anxiety',
   'can',
   'take',
   'over,',
   'so',
   'I',
   'understand',
   'mishaps.',
   'However,',
   'when',
   'employees',
   'are',
   'blatantly',
   'rude',
   'and',
   'inattentive,',
   'it',
   'should',
   'be',
   'brought',
   'to',
   'a'

In [21]:
obs = len(review_features)
obs

2765

In [25]:
train_len = round(0.8 * obs)

In [24]:
from nltk.sentiment import SentimentAnalyzer
import nltk.sentiment.util
from nltk.classify import NaiveBayesClassifier

random.shuffle(review_features)
training_docs = review_features[:train_len]
test_docs = review_features[train_len:]

print("Training: %d, Testing: %d" % (len(training_docs), len(test_docs)))

sentim_analyzer = SentimentAnalyzer()

Training: 2212, Testing: 553


In [26]:
all_words_neg = sentim_analyzer.all_words([nltk.sentiment.util.mark_negation(doc) for doc in training_docs])
all_words_neg

['Tried',
 'the',
 "chef's",
 'menu',
 '-',
 'the',
 'first',
 'sorbet',
 'was',
 'delicious,',
 'and',
 'there',
 'were',
 'a',
 'couple',
 'good',
 'dishes',
 'as',
 'well',
 'but',
 'overall',
 'all',
 'the',
 'food',
 'was',
 'deep-fried',
 'or',
 'used',
 'the',
 'fattiest',
 'part',
 'of',
 'the',
 'meat.',
 'An',
 'entire',
 'menu',
 'was',
 'very',
 'greasy',
 'and',
 'the',
 'oil/fat',
 'was',
 'staying',
 'in',
 'my',
 'mouth',
 'a',
 'whole',
 'time',
 'as',
 'deep-fried/high',
 'fat',
 'parade',
 'of',
 'the',
 'course',
 'comes',
 'to',
 'your',
 'table.',
 'The',
 'idea',
 'of',
 'the',
 'asian',
 'fusion',
 'food',
 'is',
 'unique',
 'but',
 "it's",
 'over',
 'priced',
 '(+$70',
 'after',
 'tax',
 'and',
 'tip',
 'per',
 'person',
 'without',
 'any',
 'drinks)',
 'for',
 'the',
 'quality',
 'of',
 'the',
 'food.',
 'They',
 'use',
 'a',
 'lot',
 'of',
 'truffle',
 'oil',
 'but',
 "it's",
 'not',
 'classy_NEG',
 'to_NEG',
 'use_NEG',
 'it_NEG',
 'in_NEG',
 'almost_NEG',
 

In [27]:
unigram_feats = sentim_analyzer.unigram_word_feats(all_words_neg, min_freq=4)
sentim_analyzer.add_feat_extractor(nltk.sentiment.util.extract_unigram_feats, unigrams=unigram_feats)

In [28]:
training_set = sentim_analyzer.apply_features(training_docs)
test_set = sentim_analyzer.apply_features(test_docs)

In [29]:
trainer = NaiveBayesClassifier.train
classifier = sentim_analyzer.train(trainer, training_set)
for key,value in sorted(sentim_analyzer.evaluate(test_set).items()):
     print('{0}: {1}'.format(key, value))

Training classifier
Evaluating NaiveBayesClassifier results...
Accuracy: 0.833634719710669
F-measure [negative]: 0.8302583025830258
F-measure [positive]: 0.8368794326241136
Precision [negative]: 0.8687258687258688
Precision [positive]: 0.8027210884353742
Recall [negative]: 0.7950530035335689
Recall [positive]: 0.8740740740740741
